In [2]:
getwd()

[1] "C:/Users/borrillp/TGAC_TF_analysis_2017"

In [1]:
setwd("Y:/PB_AFLF/control_timecourse/TF_analysis/phylogenetics")

In [2]:
getwd()

[1] "Y:/PB_AFLF/control_timecourse/TF_analysis/phylogenetics"

In [3]:
library("seqinr")

Warning message:
"package 'seqinr' was built under R version 3.3.3"

In [ ]:
# NB I had to install seqinr through Rstudio because I couldn't work out how to get Jupyter to install it directly, kept getting "set CRAN mirror" error

In [4]:
NAC_aln <- read.alignment(file = "Triticum_aestivum_NACs_msa_clean3.clu", format = "clustal") # read in alignment of NACs

In [24]:
NAC_aln$seq

[[1]]
[1] "---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------maqtclp-pgfr---------fhpt----------------dvelvsyylkrkimgk----------klf------------v-e--ai-sevely-kfapwdl--pd------------kscl------qs--------kdlewfffcprdk-----------------kyp---------kgs--rt--nratp-------------------------------ngywktsgkdrtielns---------------rivglkkt--------------------lifheg--------kap----------------------------------------------kgnrtdwvmye-----ykmedetl--------------------------------------------------------vs----agfskday---vlckifkksglgpri---geqy-gap------fde-n-----e-------------wen--ldv--g--ss-------if---s--------------------fap-s-------------------------sg------------ved-p--qves---------sal-at-------aivihepsapq--qsvq----------------------------------fsehv--------------------n---------------icsdqvn--------da-----pp-----------------------------------------------------------------------------------------------------eidgill---------------deltk-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------flndspn--h----------------------------------dvr------spen--------sglppm--se-------rea--------q-----------------------------------------------------------------------------------af------ei-----------nt------------------aelydq----------------------------lavlaqsg-----------d-mpaanfpa---------------------sngdviennlqq-t---ns------------glamd----dd-------yi----glddl-----fapget----------------------fs------------------------y------------------------------------------------------dfsgetf-syd--lpggtfsy-l---svpnnqfs------------qypldq-s-------sn--------g-lh------yg---dgatq-stflasgplpp------lepm------------------------------------------pstfddmpsvsnk--------------pas----------------------------------------------------------------------syclnpamkdp----------------------------------------fs*------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------"

[[2]]
[1] "---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------mgtmtlp-pgfr---------fhpt----------------ddelvgyylkrrvdnl----------kie------------l-e--vi-pvidly-kcepwel--pe------------ksfl------pk--------rdlewfffvprdr-----------------kyp---------ngs--rt--nratt-------------------------------tgywkatgkdrkvscdg---------

In [5]:
 printMultipleAlignment <- function(alignment, chunksize=60)
  {
     # this function requires the Biostrings package
     require("Biostrings")
     # find the number of sequences in the alignment
     numseqs <- alignment$nb
     # find the length of the alignment
     alignmentlen <- nchar(alignment$seq[[1]])
     starts <- seq(1, alignmentlen, by=chunksize)
     n <- length(starts)
     # get the alignment for each of the sequences:
     aln <- vector()
     lettersprinted <- vector()
     for (j in 1:numseqs)
     {
        alignmentj <- alignment$seq[[j]]
        aln[j] <- alignmentj
        lettersprinted[j] <- 0
     }
     # print out the alignment in blocks of 'chunksize' columns:
     for (i in 1:n) { # for each of n chunks
        for (j in 1:numseqs)
        {
           alnj <- aln[j]
           chunkseqjaln <- substring(alnj, starts[i], starts[i]+chunksize-1)
           chunkseqjaln <- toupper(chunkseqjaln)
           # Find out how many gaps there are in chunkseqjaln:
           gapsj <- countPattern("-",chunkseqjaln) # countPattern() is from Biostrings package
           # Calculate how many residues of the first sequence we have printed so far in the alignment:
           lettersprinted[j] <- lettersprinted[j] + chunksize - gapsj
           print(paste(chunkseqjaln,lettersprinted[j]))
        }
        print(paste(' '))
     }
  }

In [25]:
printMultipleAlignment(NAC_aln, 60)

[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "-----------------------------

In [6]:
cleanAlignment <- function(alignment, minpcnongap, minpcid)
  {
     # make a copy of the alignment to store the new alignment in:
     newalignment <- alignment
     # find the number of sequences in the alignment
     numseqs <- alignment$nb
     # empty the alignment in "newalignment")
     for (j in 1:numseqs) { newalignment$seq[[j]] <- "" }
     # find the length of the alignment
     alignmentlen <- nchar(alignment$seq[[1]])
     # look at each column of the alignment in turn:
     for (i in 1:alignmentlen)
     {
        # see what percent of the letters in this column are non-gaps:
        nongap <- 0
        for (j in 1:numseqs)
        {
           seqj <- alignment$seq[[j]]
           letterij <- substr(seqj,i,i)
           if (letterij != "-") { nongap <- nongap + 1}
        }
        pcnongap <- (nongap*100)/numseqs
        # Only consider this column if at least minpcnongap % of the letters are not gaps:
        if (pcnongap >= minpcnongap)
        {
           # see what percent of the pairs of letters in this column are identical:
           numpairs <- 0; numid <- 0
           # find the letters in all of the sequences in this column:
           for (j in 1:(numseqs-1))
           {
              seqj <- alignment$seq[[j]]
              letterij <- substr(seqj,i,i)
              for (k in (j+1):numseqs)
              {
                 seqk <- alignment$seq[[k]]
                 letterkj <- substr(seqk,i,i)
                 if (letterij != "-" && letterkj != "-")
                 {
                    numpairs <- numpairs + 1
                    if (letterij == letterkj) { numid <- numid + 1}
                 }
              }
           }
           pcid <- (numid*100)/(numpairs)
           # Only consider this column if at least %minpcid of the pairs of letters are identical:
           if (pcid >= minpcid)
           {
               for (j in 1:numseqs)
               {
                  seqj <- alignment$seq[[j]]
                  letterij <- substr(seqj,i,i)
                  newalignmentj <- newalignment$seq[[j]]
                  newalignmentj <- paste(newalignmentj,letterij,sep="")
                  newalignment$seq[[j]] <- newalignmentj
               }
           }
        }
     }
     return(newalignment)
  }

In [27]:
cleaned_NAC_aln <- cleanAlignment(NAC_aln, 80, 0)

In [28]:
?write.alignment

In [29]:
printMultipleAlignment(cleaned_NAC_aln, 60)

[1] "MAQTCLPPGFRFHPTDVELVSYYLKRKIMGKKLEAISEVELYKFAPWDLPDSCLDLEWFF 60"
[1] "MGTMTLPPGFRFHPTDDELVGYYLKRRVDNLKIEVIPVIDLYKCEPWELPESFLDLEWFF 60"
[1] "HENDLVMPGFRFHPTEEELIEFYLRRKVEGRRFELITFLDLYRFDPWELPA-MAEKEWFF 59"
[1] "QQDLQLPPGFRFHPTDEELVMHYLCRRCAGLPIPIIAEVDLYKFDPWQLPRALYEKEWYF 60"
[1] "--MAALPPGYRFYPTEEELVRFYLRHKLDGSRAEVIPVADVCSLDPWQLPEA--GEPWFY 56"
[1] "--MGELPPGYRFYPTEEELVRFYLRHMLDGRRGEVIPVADVCSLDPWQLPEA--GEPWFY 56"
[1] "PRSPDSPRGLTFAPCDADLITIYLQRKISGSPLAYIHDADVYAAEPAALVTLLPGREWYF 60"
[1] "--MAELPPGYRFYPTEEELVRFYLRHKLDGSRAEVIPVVDVCSLDPWQLPE---GEPWFY 55"
[1] "--MGELPPGYRFYPTEEELVCFYLRHMLDGRRGEVIPVVDVCSLDPWQLPEA--GEPWFY 56"
[1] "HENDLVMPGFRFHPTEEELIEFYLRRKVEGRRFELITFLDLYRFDPWELPA-MAEKEWFF 59"
[1] "QQDLQLPPGFRFHPTDEELVMHYLCRRCAGLPIPIIAEVDLYKFDPWQLPRALYEKEWYF 60"
[1] "MAQACLPPGFRFHPTDVELVSYYLKRKIMGKKLEAISEVELYKFAPWDLPDSCLDLEWFF 60"
[1] "MGTMTLPPGFRFHPTDDELVGYYLKRRVDNLKIEVIPVIDLYKCEPWELPESFLDLEWFF 60"
[1] "PRTPDSPRGLIFAPGDADLITIYLQRKISGLPLAYIHNADVYAAEPAALVTLLPGREWYF 60"
[1] "PRTPDSPRGLIFAPG

In [ ]:
# try a whole series of different percentages

In [7]:
cleaned_NAC_aln10 <- cleanAlignment(NAC_aln, 10, 0)

In [8]:
printMultipleAlignment(cleaned_NAC_aln10, 60)

Loading required package: Biostrings
Loading required package: BiocGenerics
Loading required package: parallel

Attaching package: 'BiocGenerics'

The following objects are masked from 'package:parallel':

    clusterApply, clusterApplyLB, clusterCall, clusterEvalQ,
    clusterExport, clusterMap, parApply, parCapply, parLapply,
    parLapplyLB, parRapply, parSapply, parSapplyLB

The following objects are masked from 'package:stats':

    IQR, mad, xtabs

The following objects are masked from 'package:base':

    anyDuplicated, append, as.data.frame, cbind, colnames, do.call,
    duplicated, eval, evalq, Filter, Find, get, grep, grepl, intersect,
    is.unsorted, lapply, lengths, Map, mapply, match, mget, order,
    paste, pmax, pmax.int, pmin, pmin.int, Position, rank, rbind,
    Reduce, rownames, sapply, setdiff, sort, table, tapply, union,
    unique, unsplit

Loading required package: S4Vectors
Loading required package: stats4

Attaching package: 'S4Vectors'

The following objects a

[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "--------------------------DEGSVSAATAG-----GEGGEVGD--PVAGVSDE 27"
[1] "-----LFICIWL-----------IAARVA-------SLASRARRRIEE----MSGGGGGA 33"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "--------------------------DEGSVSAATAG-----GGGGEVGG--PVAGVSDE 27"
[1] "-----------------------------------------------M----SGGGGGGS 9"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "------------------------------------------------------------ 0"
[1] "--------------------------

In [ ]:
# keeping sites with only 10% of sequences seems too low, try 20

In [ ]:
cleaned_NAC_aln20 <- cleanAlignment(cleaned_NAC_aln10, 20, 0)

In [ ]:
printMultipleAlignment(cleaned_NAC_aln20, 60)

In [ ]:
cleaned_NAC_aln30 <- cleanAlignment(cleaned_NAC_aln20, 30, 0)

In [ ]:
printMultipleAlignment(cleaned_NAC_aln30, 60)

In [ ]:
cleaned_NAC_aln40 <- cleanAlignment(cleaned_NAC_aln30, 40, 0)

In [ ]:
printMultipleAlignment(cleaned_NAC_aln40, 60)

In [ ]:
cleaned_NAC_aln50 <- cleanAlignment(cleaned_NAC_aln40, 50, 0)

In [ ]:
printMultipleAlignment(cleaned_NAC_aln50, 60)

In [ ]:
cleaned_NAC_aln60 <- cleanAlignment(cleaned_NAC_aln50, 60, 0)

In [ ]:
printMultipleAlignment(cleaned_NAC_aln60, 60)

In [ ]:
cleaned_NAC_aln70 <- cleanAlignment(cleaned_NAC_aln60, 70, 0)

In [ ]:
printMultipleAlignment(cleaned_NAC_aln70, 60)